# Regression with Keras

In [1]:
import numpy as np
from plotly.offline import init_notebook_mode, iplot
import plotly.graph_objs as go

init_notebook_mode(connected=True)

## Generate a dataset

Generate the dataset. We work with one-dimensional feature vectors, with feature values generated uniformly in $[-5,5]$. The target values will be normally distributed (mean $\mu = 0$, standard deviation $\sigma=50$) around a cubic function of the feature values, with the law

$$
y = F(x) = x^3 - \frac{1}{2}\,x^2 + 20\,x
$$

In [2]:
X = np.random.uniform(-5.0, 5.0, size=(1000,1))
Y = np.random.normal(X**3 - 5.0*X**2 + 20.0*X, 50.0)

In [3]:
trace = go.Scatter(
    x = X[:,0],
    y = Y[:,0],
    mode = 'markers',
    marker = dict(
        size = 3
    )
)

data = [trace]

layout = go.Layout(
    xaxis = dict(
        title = 'x'
    ),
    yaxis = dict(
        title = 'y'
    )
)

fig = go.Figure(data=data, layout=layout)

iplot(fig)

## Build the neural network with Keras

Keras offers an high-level interface to the underlying backend (TensorFlow in this case). A neural network is Keras is defined as a `model` object to which we can add layers to build the graph. Here we work with a feed-forward neural network built with fully connected `Dense` layers.

For general advice on nonlinear regression using Keras, see:
- https://github.com/keras-team/keras/issues/1874
- https://machinelearningmastery.com/regression-tutorial-keras-deep-learning-library-python/

In [4]:
from keras.models import Sequential
from keras.layers import Dense
from keras.metrics import mae

/opt/anaconda/envs/Python3/lib/python3.6/site-packages/h5py/__init__.py:36: FutureWarning:

Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.

Using TensorFlow backend.


For the first layer of the graph the `input_shape` keyword argument must be specified. This is a tuple of integers and does __not__ include the sample axis. Keras expects the input to have the form (n_samples, \[features\]), and `input_shape` must correspond to the shape of the features tensor.

__Example:__ if we have 50 samples, each of which is an array (tensor of rank 1 in TensorFlow terms) with 10 components, we must specify `input_shape=(10,)`.

The dimension of the last layer decides the shape of the output. Here we start with 1-dimensional inputs and we end up with 1-dimensional outputs, as we have a function $F: \mathbb{R}\to\mathbb{R}$. The hidden (intermediate) layers, on the other hand, are wider.

In [5]:
model = Sequential()
model.add(Dense(1, input_shape=(1,)))
model.add(Dense(50, activation='tanh'))
model.add(Dense(5))
model.add(Dense(1))

A common issue when doing regression with neural network is the __exploding gradients problem__, where the loss function diverges during the training phase. In this case, it was sufficient to switch from stochastic gradient descent to an Adam optimizer to solve that. The Adam optimizer is a generalization of stochastic gradient descent that exploits an adaptive learning rate.

For information about the exploding gradients problem, see:
- https://stackoverflow.com/questions/37232782/nan-loss-when-training-regression-network
- http://neuralnetworksanddeeplearning.com/chap5.html

For information about the Adam optimizer, see: https://machinelearningmastery.com/adam-optimization-algorithm-for-deep-learning/

To initialize the neural network we just call a model's `compile()` method. This include the initialization of all the weights of the layers.

In [6]:
model.compile(
    optimizer='adam',
    loss='mean_squared_error',
    metrics=['mse']
)

A model's `summary()` method gives an overview of the structure of the graph. In particular, from this we can see the number of parameters the neural network possesses.

In [7]:
model.summary()

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_1 (Dense)              (None, 1)                 2         
_________________________________________________________________
dense_2 (Dense)              (None, 50)                100       
_________________________________________________________________
dense_3 (Dense)              (None, 5)                 255       
_________________________________________________________________
dense_4 (Dense)              (None, 1)                 6         
Total params: 363
Trainable params: 363
Non-trainable params: 0
_________________________________________________________________


## Fit the neural network to the data

Keras provides an interface for training and predicting completely analogous to that of a SKLearn model. Among the options, we can specify the `epochs` parameters.

__Epochs:__ number of passages over the whole dataset the neural network will do in the training phase.

Since the dataset is small we are not dividing it in batches, meaning that each gradient descent (or Adam) step uses the exact gradient descent. This also implies that there are no stochastic features in the path followed in parameters space.

In [8]:
model.fit(X, Y, epochs=500)

Epoch 1/500
1000/1000 [==============================] - 1s 510us/step - loss: 15680.2884 - mean_squared_error: 15680.2884
Epoch 2/500
1000/1000 [==============================] - 0s 55us/step - loss: 15214.1194 - mean_squared_error: 15214.1194
Epoch 3/500
1000/1000 [==============================] - 0s 46us/step - loss: 14591.7928 - mean_squared_error: 14591.7928
Epoch 4/500
1000/1000 [==============================] - 0s 45us/step - loss: 13795.7040 - mean_squared_error: 13795.7040
Epoch 5/500
1000/1000 [==============================] - 0s 42us/step - loss: 12816.8189 - mean_squared_error: 12816.8189
Epoch 6/500
1000/1000 [==============================] - 0s 43us/step - loss: 11766.2801 - mean_squared_error: 11766.2801
Epoch 7/500
1000/1000 [==============================] - 0s 40us/step - loss: 10757.6802 - mean_squared_error: 10757.6802
Epoch 8/500
1000/1000 [==============================] - 0s 40us/step - loss: 9825.0122 - mean_squared_error: 9825.0122
Epoch 9/500
1000/1000 [==

1000/1000 [==============================] - 0s 47us/step - loss: 2727.6071 - mean_squared_error: 2727.6071
Epoch 69/500
1000/1000 [==============================] - 0s 42us/step - loss: 2720.9501 - mean_squared_error: 2720.9501
Epoch 70/500
1000/1000 [==============================] - 0s 42us/step - loss: 2699.1766 - mean_squared_error: 2699.1766
Epoch 71/500
1000/1000 [==============================] - 0s 44us/step - loss: 2685.5676 - mean_squared_error: 2685.5676
Epoch 72/500
1000/1000 [==============================] - 0s 44us/step - loss: 2674.2481 - mean_squared_error: 2674.2481
Epoch 73/500
1000/1000 [==============================] - 0s 44us/step - loss: 2670.5857 - mean_squared_error: 2670.5857
Epoch 74/500
1000/1000 [==============================] - 0s 40us/step - loss: 2653.8937 - mean_squared_error: 2653.8937
Epoch 75/500
1000/1000 [==============================] - 0s 43us/step - loss: 2645.1707 - mean_squared_error: 2645.1707
Epoch 76/500
1000/1000 [=====================

1000/1000 [==============================] - 0s 43us/step - loss: 2440.3375 - mean_squared_error: 2440.3375
Epoch 136/500
1000/1000 [==============================] - 0s 42us/step - loss: 2424.9647 - mean_squared_error: 2424.9647
Epoch 137/500
1000/1000 [==============================] - 0s 41us/step - loss: 2420.1793 - mean_squared_error: 2420.1793
Epoch 138/500
1000/1000 [==============================] - 0s 44us/step - loss: 2422.4230 - mean_squared_error: 2422.4230
Epoch 139/500
1000/1000 [==============================] - 0s 43us/step - loss: 2423.9968 - mean_squared_error: 2423.9968
Epoch 140/500
1000/1000 [==============================] - 0s 42us/step - loss: 2421.0932 - mean_squared_error: 2421.0932
Epoch 141/500
1000/1000 [==============================] - 0s 42us/step - loss: 2428.0396 - mean_squared_error: 2428.0396
Epoch 142/500
1000/1000 [==============================] - 0s 42us/step - loss: 2410.9513 - mean_squared_error: 2410.9513
Epoch 143/500
1000/1000 [=============

1000/1000 [==============================] - 0s 45us/step - loss: 2393.2574 - mean_squared_error: 2393.2574
Epoch 203/500
1000/1000 [==============================] - 0s 41us/step - loss: 2388.4269 - mean_squared_error: 2388.4269
Epoch 204/500
1000/1000 [==============================] - 0s 42us/step - loss: 2393.5049 - mean_squared_error: 2393.5049
Epoch 205/500
1000/1000 [==============================] - 0s 42us/step - loss: 2402.7443 - mean_squared_error: 2402.7443
Epoch 206/500
1000/1000 [==============================] - 0s 43us/step - loss: 2395.1050 - mean_squared_error: 2395.1050
Epoch 207/500
1000/1000 [==============================] - 0s 42us/step - loss: 2385.5595 - mean_squared_error: 2385.5595
Epoch 208/500
1000/1000 [==============================] - 0s 43us/step - loss: 2393.5255 - mean_squared_error: 2393.5255
Epoch 209/500
1000/1000 [==============================] - 0s 43us/step - loss: 2392.9190 - mean_squared_error: 2392.9190
Epoch 210/500
1000/1000 [=============

1000/1000 [==============================] - 0s 42us/step - loss: 2383.5141 - mean_squared_error: 2383.5141
Epoch 270/500
1000/1000 [==============================] - 0s 42us/step - loss: 2393.1711 - mean_squared_error: 2393.1711
Epoch 271/500
1000/1000 [==============================] - 0s 42us/step - loss: 2387.3799 - mean_squared_error: 2387.3799
Epoch 272/500
1000/1000 [==============================] - 0s 42us/step - loss: 2381.2715 - mean_squared_error: 2381.2715
Epoch 273/500
1000/1000 [==============================] - 0s 42us/step - loss: 2387.4790 - mean_squared_error: 2387.4790
Epoch 274/500
1000/1000 [==============================] - 0s 42us/step - loss: 2388.5395 - mean_squared_error: 2388.5395
Epoch 275/500
1000/1000 [==============================] - 0s 42us/step - loss: 2384.8832 - mean_squared_error: 2384.8832
Epoch 276/500
1000/1000 [==============================] - 0s 43us/step - loss: 2393.7828 - mean_squared_error: 2393.7828
Epoch 277/500
1000/1000 [=============

1000/1000 [==============================] - 0s 43us/step - loss: 2382.6037 - mean_squared_error: 2382.6037
Epoch 337/500
1000/1000 [==============================] - 0s 48us/step - loss: 2385.3101 - mean_squared_error: 2385.3101
Epoch 338/500
1000/1000 [==============================] - 0s 41us/step - loss: 2383.2224 - mean_squared_error: 2383.2224
Epoch 339/500
1000/1000 [==============================] - 0s 42us/step - loss: 2382.7922 - mean_squared_error: 2382.7922
Epoch 340/500
1000/1000 [==============================] - 0s 42us/step - loss: 2381.6553 - mean_squared_error: 2381.6553
Epoch 341/500
1000/1000 [==============================] - 0s 43us/step - loss: 2386.9977 - mean_squared_error: 2386.9977
Epoch 342/500
1000/1000 [==============================] - 0s 44us/step - loss: 2383.6446 - mean_squared_error: 2383.6446
Epoch 343/500
1000/1000 [==============================] - 0s 42us/step - loss: 2378.6896 - mean_squared_error: 2378.6896
Epoch 344/500
1000/1000 [=============

1000/1000 [==============================] - 0s 42us/step - loss: 2392.4406 - mean_squared_error: 2392.4406
Epoch 404/500
1000/1000 [==============================] - 0s 44us/step - loss: 2378.2541 - mean_squared_error: 2378.2541
Epoch 405/500
1000/1000 [==============================] - 0s 44us/step - loss: 2390.4498 - mean_squared_error: 2390.4498
Epoch 406/500
1000/1000 [==============================] - 0s 47us/step - loss: 2384.9290 - mean_squared_error: 2384.9290
Epoch 407/500
1000/1000 [==============================] - 0s 43us/step - loss: 2382.6714 - mean_squared_error: 2382.6714
Epoch 408/500
1000/1000 [==============================] - 0s 44us/step - loss: 2388.2425 - mean_squared_error: 2388.2425
Epoch 409/500
1000/1000 [==============================] - 0s 44us/step - loss: 2380.0947 - mean_squared_error: 2380.0947
Epoch 410/500
1000/1000 [==============================] - 0s 41us/step - loss: 2387.8129 - mean_squared_error: 2387.8129
Epoch 411/500
1000/1000 [=============

1000/1000 [==============================] - 0s 40us/step - loss: 2379.0905 - mean_squared_error: 2379.0905
Epoch 471/500
1000/1000 [==============================] - 0s 42us/step - loss: 2380.1455 - mean_squared_error: 2380.1455
Epoch 472/500
1000/1000 [==============================] - 0s 42us/step - loss: 2390.3310 - mean_squared_error: 2390.3310
Epoch 473/500
1000/1000 [==============================] - 0s 42us/step - loss: 2379.2884 - mean_squared_error: 2379.2884
Epoch 474/500
1000/1000 [==============================] - 0s 41us/step - loss: 2379.5016 - mean_squared_error: 2379.5016
Epoch 475/500
1000/1000 [==============================] - 0s 41us/step - loss: 2380.2113 - mean_squared_error: 2380.2113
Epoch 476/500
1000/1000 [==============================] - 0s 42us/step - loss: 2383.3550 - mean_squared_error: 2383.3550
Epoch 477/500
1000/1000 [==============================] - 0s 43us/step - loss: 2378.1519 - mean_squared_error: 2378.1519
Epoch 478/500
1000/1000 [=============

## Generate a new dataset and get predictions

To check whether the neural network did a good job, we can make prediction over a (1-dimensional) grid of values and compare it with the true value of the function to fit on the same grid.

In [9]:
X_pred = np.linspace(-10.0, 10.0, 1000).reshape((1000,1))
Y_pred = model.predict(X_pred)

In [10]:
def f_to_fit(x):
    return x**3 - 5.0*x**2 + 20.0*x

In [11]:
trace_data = go.Scatter(
    x = X[:,0],
    y = Y[:,0],
    mode = 'markers',
    marker = dict(
        size = 3
    ),
    name = 'data'
)

trace_pred = go.Scatter(
    x = X_pred[:,0],
    y = Y_pred[:,0],
    mode = 'markers',
    marker = dict(
        size = 3
    ),
    name = 'predictions'
)

trace_true = go.Scatter(
    x = X_pred[:,0],
    y = f_to_fit(X_pred)[:,0],
    mode = 'markers',
    marker = dict(
        size = 3
    ),
    name = 'true values'
)

data = [trace_data, trace_pred, trace_true]

layout = go.Layout(
    xaxis = dict(
        title = 'x'
    ),
    yaxis = dict(
        title = 'y'
    ),
    hovermode = 'closest'
)

fig = go.Figure(data=data, layout=layout)

iplot(fig)

### Comments: overfitting?

A question is in order on whether by looking at the plot above we should think we are overfitting the data. Notice that no cross validation (train-test split) has been done: we are just comparing the predictions from the neural network with the true, deterministic form of the function we wanted to fit. Ultimately, the question we would like to answer is: __given the data, can the neural network learn the true form of the function?__

In the region where datapoints are present, the fit to the data is good and there's good correspondence with the deterministic function as well: to see if there's overfitting here we should do cross validation on the dataset.

In the region where no datapoint is present, the predictions do not match the deterministic function. In my view, this is somewhat expected: approximating functions with functions of a different form usually requires series (power series, trigonometric series etc.). The prediction of the neural networks, as a function of the input, is just not a cubic, therefore shouldn't be expected to match it in an arbitrary large domain.

## More experiments

We can tweak the topology of the graph and the number of epochs to see how the results vary. The best generalization seems to be the one using wider layers with `tanh` activation function followed by narrower linear layers.

In [12]:
model_2 = Sequential()
model_2.add(Dense(1, input_shape=(1,)))
model_2.add(Dense(10, activation='tanh'))
model_2.add(Dense(5))
model_2.add(Dense(10, activation='tanh'))
model_2.add(Dense(5))
model_2.add(Dense(10, activation='tanh'))
model_2.add(Dense(5))
model_2.add(Dense(1))

model_2.compile(
    optimizer='adam',
    loss='mean_squared_error',
    metrics=['mse']
)

model_2.fit(X, Y, epochs=500)

Epoch 1/500
1000/1000 [==============================] - 1s 837us/step - loss: 15643.9757 - mean_squared_error: 15643.9757
Epoch 2/500
1000/1000 [==============================] - 0s 57us/step - loss: 15274.3924 - mean_squared_error: 15274.3924
Epoch 3/500
1000/1000 [==============================] - 0s 55us/step - loss: 14873.3183 - mean_squared_error: 14873.3183
Epoch 4/500
1000/1000 [==============================] - 0s 58us/step - loss: 14440.0964 - mean_squared_error: 14440.0964
Epoch 5/500
1000/1000 [==============================] - 0s 57us/step - loss: 14044.0453 - mean_squared_error: 14044.0453
Epoch 6/500
1000/1000 [==============================] - 0s 56us/step - loss: 13667.3682 - mean_squared_error: 13667.3682
Epoch 7/500
1000/1000 [==============================] - 0s 58us/step - loss: 13312.5128 - mean_squared_error: 13312.5128
Epoch 8/500
1000/1000 [==============================] - 0s 58us/step - loss: 12956.6017 - mean_squared_error: 12956.6017
Epoch 9/500
1000/1000 [

1000/1000 [==============================] - 0s 58us/step - loss: 2710.0457 - mean_squared_error: 2710.0457
Epoch 69/500
1000/1000 [==============================] - 0s 58us/step - loss: 2698.6525 - mean_squared_error: 2698.6525
Epoch 70/500
1000/1000 [==============================] - 0s 58us/step - loss: 2690.5172 - mean_squared_error: 2690.5172
Epoch 71/500
1000/1000 [==============================] - 0s 63us/step - loss: 2670.7157 - mean_squared_error: 2670.7157
Epoch 72/500
1000/1000 [==============================] - 0s 56us/step - loss: 2670.2772 - mean_squared_error: 2670.2772
Epoch 73/500
1000/1000 [==============================] - 0s 58us/step - loss: 2651.8599 - mean_squared_error: 2651.8599
Epoch 74/500
1000/1000 [==============================] - 0s 57us/step - loss: 2626.7715 - mean_squared_error: 2626.7715
Epoch 75/500
1000/1000 [==============================] - 0s 58us/step - loss: 2658.2635 - mean_squared_error: 2658.2635
Epoch 76/500
1000/1000 [=====================

1000/1000 [==============================] - 0s 58us/step - loss: 2408.1094 - mean_squared_error: 2408.1094
Epoch 136/500
1000/1000 [==============================] - 0s 59us/step - loss: 2426.5575 - mean_squared_error: 2426.5575
Epoch 137/500
1000/1000 [==============================] - 0s 55us/step - loss: 2412.9679 - mean_squared_error: 2412.9679
Epoch 138/500
1000/1000 [==============================] - 0s 57us/step - loss: 2402.6838 - mean_squared_error: 2402.6838
Epoch 139/500
1000/1000 [==============================] - 0s 58us/step - loss: 2408.3318 - mean_squared_error: 2408.3318
Epoch 140/500
1000/1000 [==============================] - 0s 57us/step - loss: 2406.4595 - mean_squared_error: 2406.4595
Epoch 141/500
1000/1000 [==============================] - 0s 57us/step - loss: 2420.6234 - mean_squared_error: 2420.6234
Epoch 142/500
1000/1000 [==============================] - 0s 57us/step - loss: 2416.1763 - mean_squared_error: 2416.1763
Epoch 143/500
1000/1000 [=============

1000/1000 [==============================] - 0s 55us/step - loss: 2481.3889 - mean_squared_error: 2481.3889
Epoch 203/500
1000/1000 [==============================] - 0s 67us/step - loss: 2379.7932 - mean_squared_error: 2379.7932
Epoch 204/500
1000/1000 [==============================] - 0s 56us/step - loss: 2405.4215 - mean_squared_error: 2405.4215
Epoch 205/500
1000/1000 [==============================] - 0s 57us/step - loss: 2400.4390 - mean_squared_error: 2400.4390
Epoch 206/500
1000/1000 [==============================] - 0s 58us/step - loss: 2381.9338 - mean_squared_error: 2381.9338
Epoch 207/500
1000/1000 [==============================] - 0s 57us/step - loss: 2387.3092 - mean_squared_error: 2387.3092
Epoch 208/500
1000/1000 [==============================] - 0s 57us/step - loss: 2404.9129 - mean_squared_error: 2404.9129
Epoch 209/500
1000/1000 [==============================] - 0s 58us/step - loss: 2380.5351 - mean_squared_error: 2380.5351
Epoch 210/500
1000/1000 [=============

1000/1000 [==============================] - 0s 57us/step - loss: 2377.8118 - mean_squared_error: 2377.8118
Epoch 270/500
1000/1000 [==============================] - 0s 56us/step - loss: 2376.5646 - mean_squared_error: 2376.5646
Epoch 271/500
1000/1000 [==============================] - 0s 57us/step - loss: 2382.0839 - mean_squared_error: 2382.0839
Epoch 272/500
1000/1000 [==============================] - 0s 58us/step - loss: 2365.9496 - mean_squared_error: 2365.9496
Epoch 273/500
1000/1000 [==============================] - 0s 57us/step - loss: 2361.8164 - mean_squared_error: 2361.8164
Epoch 274/500
1000/1000 [==============================] - 0s 58us/step - loss: 2368.1713 - mean_squared_error: 2368.1713
Epoch 275/500
1000/1000 [==============================] - 0s 58us/step - loss: 2372.1862 - mean_squared_error: 2372.1862
Epoch 276/500
1000/1000 [==============================] - 0s 57us/step - loss: 2376.7103 - mean_squared_error: 2376.7103
Epoch 277/500
1000/1000 [=============

1000/1000 [==============================] - 0s 58us/step - loss: 2359.8586 - mean_squared_error: 2359.8586
Epoch 337/500
1000/1000 [==============================] - 0s 59us/step - loss: 2367.8421 - mean_squared_error: 2367.8421
Epoch 338/500
1000/1000 [==============================] - 0s 57us/step - loss: 2375.2587 - mean_squared_error: 2375.2587
Epoch 339/500
1000/1000 [==============================] - 0s 58us/step - loss: 2370.2398 - mean_squared_error: 2370.2398
Epoch 340/500
1000/1000 [==============================] - 0s 59us/step - loss: 2387.0616 - mean_squared_error: 2387.0616
Epoch 341/500
1000/1000 [==============================] - 0s 57us/step - loss: 2390.7715 - mean_squared_error: 2390.7715
Epoch 342/500
1000/1000 [==============================] - 0s 57us/step - loss: 2400.7149 - mean_squared_error: 2400.7149
Epoch 343/500
1000/1000 [==============================] - 0s 57us/step - loss: 2415.7590 - mean_squared_error: 2415.7590
Epoch 344/500
1000/1000 [=============

1000/1000 [==============================] - 0s 59us/step - loss: 2368.9906 - mean_squared_error: 2368.9906
Epoch 404/500
1000/1000 [==============================] - 0s 59us/step - loss: 2370.5476 - mean_squared_error: 2370.5476
Epoch 405/500
1000/1000 [==============================] - 0s 58us/step - loss: 2374.4730 - mean_squared_error: 2374.4730
Epoch 406/500
1000/1000 [==============================] - 0s 60us/step - loss: 2372.1541 - mean_squared_error: 2372.1541
Epoch 407/500
1000/1000 [==============================] - 0s 57us/step - loss: 2377.9471 - mean_squared_error: 2377.9471
Epoch 408/500
1000/1000 [==============================] - 0s 58us/step - loss: 2409.0467 - mean_squared_error: 2409.0467
Epoch 409/500
1000/1000 [==============================] - 0s 57us/step - loss: 2385.8046 - mean_squared_error: 2385.8046
Epoch 410/500
1000/1000 [==============================] - 0s 57us/step - loss: 2373.2549 - mean_squared_error: 2373.2549
Epoch 411/500
1000/1000 [=============

1000/1000 [==============================] - 0s 57us/step - loss: 2365.2270 - mean_squared_error: 2365.2270
Epoch 471/500
1000/1000 [==============================] - 0s 55us/step - loss: 2376.9500 - mean_squared_error: 2376.9500
Epoch 472/500
1000/1000 [==============================] - 0s 55us/step - loss: 2410.8069 - mean_squared_error: 2410.8069
Epoch 473/500
1000/1000 [==============================] - 0s 57us/step - loss: 2418.0066 - mean_squared_error: 2418.0066
Epoch 474/500
1000/1000 [==============================] - 0s 59us/step - loss: 2388.1308 - mean_squared_error: 2388.1308
Epoch 475/500
1000/1000 [==============================] - 0s 57us/step - loss: 2354.8329 - mean_squared_error: 2354.8329
Epoch 476/500
1000/1000 [==============================] - 0s 56us/step - loss: 2363.1411 - mean_squared_error: 2363.1411
Epoch 477/500
1000/1000 [==============================] - 0s 56us/step - loss: 2372.4819 - mean_squared_error: 2372.4819
Epoch 478/500
1000/1000 [=============

In [13]:
Y_pred = model_2.predict(X_pred)

trace_data = go.Scatter(
    x = X[:,0],
    y = Y[:,0],
    mode = 'markers',
    marker = dict(
        size = 3
    ),
    name = 'data'
)

trace_pred = go.Scatter(
    x = X_pred[:,0],
    y = Y_pred[:,0],
    mode = 'markers',
    marker = dict(
        size = 3
    ),
    name = 'predictions'
)

trace_true = go.Scatter(
    x = X_pred[:,0],
    y = f_to_fit(X_pred)[:,0],
    mode = 'markers',
    marker = dict(
        size = 3
    ),
    name = 'true values'
)

data = [trace_data, trace_pred, trace_true]

layout = go.Layout(
    xaxis = dict(
        title = 'x'
    ),
    yaxis = dict(
        title = 'y'
    ),
    hovermode = 'closest'
)

fig = go.Figure(data=data, layout=layout)

iplot(fig)

## Regression on no-noise data

Let's see what happens if, instead of generating data with target values distributed (normally) around a deterministic function of the feature values, we train the neural network with data exactly following that function.

In [14]:
X_det = np.linspace(-5.0, 5.0, 1000).reshape((1000,1))
Y_det = f_to_fit(X_det)

In [15]:
trace = go.Scatter(
    x = X_det[:,0],
    y = Y_det[:,0],
    mode = 'markers',
    marker = dict(
        size = 3
    )
)

data = [trace]

layout = go.Layout(
    xaxis = dict(
        title = 'x'
    ),
    yaxis = dict(
        title = 'y'
    )
)

fig = go.Figure(data=data, layout=layout)

iplot(fig)

In [16]:
model_det = Sequential()
model_det.add(Dense(1, input_shape=(1,)))
model_det.add(Dense(10, activation='tanh'))
model_det.add(Dense(5))
model_det.add(Dense(10, activation='tanh'))
model_det.add(Dense(5))
model_det.add(Dense(10, activation='tanh'))
model_det.add(Dense(5))
model_det.add(Dense(1))

In [17]:
model_det.compile(
    optimizer='adam',
    loss='mean_squared_error',
    metrics=['mse']
)

model_det.fit(X_det, Y_det, epochs=500)

Epoch 1/500
1000/1000 [==============================] - 1s 843us/step - loss: 13719.5997 - mean_squared_error: 13719.5997
Epoch 2/500
1000/1000 [==============================] - 0s 72us/step - loss: 13610.0174 - mean_squared_error: 13610.0174
Epoch 3/500
1000/1000 [==============================] - 0s 63us/step - loss: 13473.5022 - mean_squared_error: 13473.5022
Epoch 4/500
1000/1000 [==============================] - 0s 59us/step - loss: 13305.9312 - mean_squared_error: 13305.9312
Epoch 5/500
1000/1000 [==============================] - 0s 60us/step - loss: 13103.6830 - mean_squared_error: 13103.6830
Epoch 6/500
1000/1000 [==============================] - 0s 62us/step - loss: 12870.9126 - mean_squared_error: 12870.9126
Epoch 7/500
1000/1000 [==============================] - 0s 60us/step - loss: 12610.4060 - mean_squared_error: 12610.4060
Epoch 8/500
1000/1000 [==============================] - 0s 58us/step - loss: 12311.1761 - mean_squared_error: 12311.1761
Epoch 9/500
1000/1000 [

1000/1000 [==============================] - 0s 58us/step - loss: 345.7856 - mean_squared_error: 345.7856
Epoch 69/500
1000/1000 [==============================] - 0s 56us/step - loss: 321.7896 - mean_squared_error: 321.7896
Epoch 70/500
1000/1000 [==============================] - 0s 58us/step - loss: 299.4236 - mean_squared_error: 299.4236
Epoch 71/500
1000/1000 [==============================] - 0s 57us/step - loss: 279.0419 - mean_squared_error: 279.0419
Epoch 72/500
1000/1000 [==============================] - 0s 58us/step - loss: 259.3298 - mean_squared_error: 259.3298
Epoch 73/500
1000/1000 [==============================] - 0s 57us/step - loss: 242.6516 - mean_squared_error: 242.6516
Epoch 74/500
1000/1000 [==============================] - 0s 57us/step - loss: 225.1983 - mean_squared_error: 225.1983
Epoch 75/500
1000/1000 [==============================] - 0s 58us/step - loss: 209.3005 - mean_squared_error: 209.3005
Epoch 76/500
1000/1000 [==============================] - 0s 

1000/1000 [==============================] - 0s 59us/step - loss: 4.9592 - mean_squared_error: 4.9592
Epoch 138/500
1000/1000 [==============================] - 0s 57us/step - loss: 4.6317 - mean_squared_error: 4.6317
Epoch 139/500
1000/1000 [==============================] - 0s 57us/step - loss: 4.6822 - mean_squared_error: 4.6822
Epoch 140/500
1000/1000 [==============================] - 0s 59us/step - loss: 4.6908 - mean_squared_error: 4.6908
Epoch 141/500
1000/1000 [==============================] - 0s 56us/step - loss: 5.0362 - mean_squared_error: 5.0362
Epoch 142/500
1000/1000 [==============================] - 0s 57us/step - loss: 5.5196 - mean_squared_error: 5.5196
Epoch 143/500
1000/1000 [==============================] - 0s 61us/step - loss: 4.1986 - mean_squared_error: 4.1986
Epoch 144/500
1000/1000 [==============================] - 0s 65us/step - loss: 3.6288 - mean_squared_error: 3.6288
Epoch 145/500
1000/1000 [==============================] - 0s 62us/step - loss: 3.5512

1000/1000 [==============================] - 0s 56us/step - loss: 1.7433 - mean_squared_error: 1.7433
Epoch 208/500
1000/1000 [==============================] - 0s 61us/step - loss: 0.7268 - mean_squared_error: 0.7268
Epoch 209/500
1000/1000 [==============================] - 0s 59us/step - loss: 0.7405 - mean_squared_error: 0.7405
Epoch 210/500
1000/1000 [==============================] - 0s 59us/step - loss: 0.6283 - mean_squared_error: 0.6283
Epoch 211/500
1000/1000 [==============================] - 0s 58us/step - loss: 1.0918 - mean_squared_error: 1.0918
Epoch 212/500
1000/1000 [==============================] - 0s 58us/step - loss: 1.1621 - mean_squared_error: 1.1621
Epoch 213/500
1000/1000 [==============================] - 0s 58us/step - loss: 1.3392 - mean_squared_error: 1.3392
Epoch 214/500
1000/1000 [==============================] - 0s 57us/step - loss: 0.6306 - mean_squared_error: 0.6306
Epoch 215/500
1000/1000 [==============================] - 0s 64us/step - loss: 0.5004

1000/1000 [==============================] - 0s 57us/step - loss: 0.2909 - mean_squared_error: 0.2909
Epoch 278/500
1000/1000 [==============================] - 0s 57us/step - loss: 0.2353 - mean_squared_error: 0.2353
Epoch 279/500
1000/1000 [==============================] - 0s 56us/step - loss: 0.1848 - mean_squared_error: 0.1848
Epoch 280/500
1000/1000 [==============================] - 0s 57us/step - loss: 0.2942 - mean_squared_error: 0.2942
Epoch 281/500
1000/1000 [==============================] - 0s 57us/step - loss: 0.3467 - mean_squared_error: 0.3467
Epoch 282/500
1000/1000 [==============================] - 0s 56us/step - loss: 0.2196 - mean_squared_error: 0.2196
Epoch 283/500
1000/1000 [==============================] - 0s 56us/step - loss: 0.3373 - mean_squared_error: 0.3373
Epoch 284/500
1000/1000 [==============================] - 0s 57us/step - loss: 0.2478 - mean_squared_error: 0.2478
Epoch 285/500
1000/1000 [==============================] - 0s 57us/step - loss: 0.2624

1000/1000 [==============================] - 0s 59us/step - loss: 0.4373 - mean_squared_error: 0.4373
Epoch 348/500
1000/1000 [==============================] - 0s 58us/step - loss: 0.1515 - mean_squared_error: 0.1515
Epoch 349/500
1000/1000 [==============================] - 0s 58us/step - loss: 0.1861 - mean_squared_error: 0.1861
Epoch 350/500
1000/1000 [==============================] - 0s 57us/step - loss: 0.1212 - mean_squared_error: 0.1212
Epoch 351/500
1000/1000 [==============================] - 0s 57us/step - loss: 0.1658 - mean_squared_error: 0.1658
Epoch 352/500
1000/1000 [==============================] - 0s 58us/step - loss: 0.2210 - mean_squared_error: 0.2210
Epoch 353/500
1000/1000 [==============================] - 0s 57us/step - loss: 0.9726 - mean_squared_error: 0.9726
Epoch 354/500
1000/1000 [==============================] - 0s 56us/step - loss: 0.1791 - mean_squared_error: 0.1791
Epoch 355/500
1000/1000 [==============================] - 0s 57us/step - loss: 0.3459

1000/1000 [==============================] - 0s 60us/step - loss: 0.0652 - mean_squared_error: 0.0652
Epoch 418/500
1000/1000 [==============================] - 0s 56us/step - loss: 0.0814 - mean_squared_error: 0.0814
Epoch 419/500
1000/1000 [==============================] - 0s 56us/step - loss: 0.1262 - mean_squared_error: 0.1262
Epoch 420/500
1000/1000 [==============================] - 0s 56us/step - loss: 0.2281 - mean_squared_error: 0.2281
Epoch 421/500
1000/1000 [==============================] - 0s 60us/step - loss: 0.1571 - mean_squared_error: 0.1571
Epoch 422/500
1000/1000 [==============================] - 0s 56us/step - loss: 0.1001 - mean_squared_error: 0.1001
Epoch 423/500
1000/1000 [==============================] - 0s 61us/step - loss: 0.0638 - mean_squared_error: 0.0638
Epoch 424/500
1000/1000 [==============================] - 0s 59us/step - loss: 0.0700 - mean_squared_error: 0.0700
Epoch 425/500
1000/1000 [==============================] - 0s 57us/step - loss: 0.0828

1000/1000 [==============================] - 0s 61us/step - loss: 0.0622 - mean_squared_error: 0.0622
Epoch 488/500
1000/1000 [==============================] - 0s 56us/step - loss: 0.1788 - mean_squared_error: 0.1788
Epoch 489/500
1000/1000 [==============================] - 0s 60us/step - loss: 0.9577 - mean_squared_error: 0.9577
Epoch 490/500
1000/1000 [==============================] - 0s 58us/step - loss: 0.6176 - mean_squared_error: 0.6176
Epoch 491/500
1000/1000 [==============================] - 0s 58us/step - loss: 0.1869 - mean_squared_error: 0.1869
Epoch 492/500
1000/1000 [==============================] - 0s 56us/step - loss: 0.9431 - mean_squared_error: 0.9431
Epoch 493/500
1000/1000 [==============================] - 0s 57us/step - loss: 0.2928 - mean_squared_error: 0.2928
Epoch 494/500
1000/1000 [==============================] - 0s 61us/step - loss: 0.1248 - mean_squared_error: 0.1248
Epoch 495/500
1000/1000 [==============================] - 0s 66us/step - loss: 0.0534

In [18]:
X_pred = np.linspace(-10.0, 10.0, 1000).reshape((1000,1))
Y_pred = model_det.predict(X_pred)

trace_data = go.Scatter(
    x = X_det[:,0],
    y = Y_det[:,0],
    mode = 'markers',
    marker = dict(
        size = 3
    ),
    name = 'data'
)

trace_pred = go.Scatter(
    x = X_pred[:,0],
    y = Y_pred[:,0],
    mode = 'markers',
    marker = dict(
        size = 3
    ),
    name = 'predictions'
)

trace_true = go.Scatter(
    x = X_pred[:,0],
    y = f_to_fit(X_pred)[:,0],
    mode = 'markers',
    marker = dict(
        size = 3
    ),
    name = 'true values'
)

data = [trace_data, trace_pred, trace_true]

layout = go.Layout(
    xaxis = dict(
        title = 'x'
    ),
    yaxis = dict(
        title = 'y'
    ),
    hovermode = 'closest'
)

fig = go.Figure(data=data, layout=layout)

iplot(fig)

### Conclusion

Even with data completely devoid of noise, the neural network provides predictions that do not match the true function outside of the region where the datapoint are present. This again signifies that the model does a good job at fitting what it sees but hasn't learned the true underlying rule: you need a cubic to fully understand a cubic!

## Higher dimensional data

Neural networks can deal effectively with high dimensional data (images, audio, video). As an experiment, let's run a regression on 2-dimensional data with a function of the form

$$
G(x) = \log\left( x^2 + y^2\right)
$$

In [19]:
def g_to_fit(x, y):
    return np.log(x**2+y**2)

In [20]:
X_coords = np.random.uniform(-5.0, 5.0, 100)
Y_coords = np.random.uniform(-5.0, 5.0, 100)

Xv_g, Yv_g = np.meshgrid(X_coords, Y_coords, indexing='ij')

In [35]:
trace = go.Scatter3d(
    x = Xv_g.ravel(),
    y = Yv_g.ravel(),
    z = g_to_fit(Xv_g.ravel(), Yv_g.ravel()),
    mode = 'markers',
    marker = dict(
        size=3
    )
)

layout = go.Layout(
    scene = dict(
        xaxis = dict(
            title = 'x'
        ),
        yaxis = dict(
            title = 'y'
        ),
        zaxis = dict(
            title = 'z=G(x,y)'
        )
    )
)

data = [trace]

fig = go.Figure(data=data, layout=layout)

iplot(fig)

In [32]:
X_g = []

for x, y in np.nditer([Xv_g, Yv_g]):
    X_g.append([float(x), float(y)])

#Input variables
X_g = np.array(X_g)

#Target variables
Y_g = np.random.normal(g_to_fit(X_g[:,0], X_g[:,1]), scale=0.5)

In [34]:
trace = go.Scatter3d(
    x = X_g[:,0],
    y = X_g[:,1],
    z = Y_g,
    mode = 'markers',
    marker = dict(
        size=3
    )
)

layout = go.Layout(
    scene = dict(
        xaxis = dict(
            title = 'x'
        ),
        yaxis = dict(
            title = 'y'
        ),
        zaxis = dict(
            title = 'z=G(x,y)'
        )
    )
)

data = [trace]

fig = go.Figure(data=data, layout=layout)

iplot(fig)